In [44]:
from openvino.inference_engine import IECore
import cv2 as cv
import numpy as np
import time

import sys
from util import ResizeImage,CropImage,ToTensor,NormalizeImage
from PIL import Image

image_file = "test/test1.png"
top_k = 5

DEVICE = 'CPU'
#初始化插件，输出插件版本号
ie = IECore()
devices = ie.available_devices
print(devices)
ver = ie.get_versions(DEVICE)[DEVICE]
print("{descr}: {maj}.{min}.{num}".format(descr=ver.description, maj=ver.major, min=ver.minor, num=ver.build_number))



['CPU', 'GNA', 'GPU']
MKLDNNPlugin: 2.1.2021.3.0-2787-60059f2c755-releases/2021/3


In [45]:
# 图像预处理，转为Tensor张量
def preprocess(img):
    resize_op = ResizeImage(resize_short=224)
    img = resize_op(img)
    img_mean = [0.877, 0.877, 0.877]
    img_std = [0.200, 0.200, 0.200]
    img_scale = 1.0 / 255.0
    normalize_op = NormalizeImage(
        scale=img_scale, mean=img_mean, std=img_std)
    img = normalize_op(img)
    tensor_op = ToTensor()
    img = tensor_op(img)
    return img

# 减少图像白边
def cutImg(img):
    dst = 255- img
    gray = cv.cvtColor(dst,cv.COLOR_BGR2GRAY)  
    ret, binary = cv.threshold(gray,127,255,cv.THRESH_BINARY)  
    
    contours, hierarchy = cv.findContours(binary,cv.RETR_TREE,cv.CHAIN_APPROX_SIMPLE)

    minx = 65523
    miny = 65523
    maxx = 0
    maxy = 0

    for contour in contours:
        boundRect = cv.boundingRect(contour)
        (x,y,w,h)=boundRect
        if x<minx:
            minx=x
        if y<miny:
            miny=y
        if x+w>maxx:
            maxx=x+w
        if y+h>maxy:
            maxy=y+h
    cutw=maxx-minx
    cuth=maxy-miny
    # w>h
    # if cutw>cuth:
    #     cuty1=int((maxy+miny)/2-cutw/2)
    #     cuty2=int((maxy+miny)/2+cutw/2)
    #     img = img[cuty1:cuty2,minx:maxx]
    # if cutw<cuth:
    #     cutx1=int((maxx+minx)/2-cuth/2)
    #     cutx2=int((maxx+minx)/2+cuth/2)
    #     img = img[miny:maxy,cutx1:cutx2] 
    img = img[miny:maxy,minx:maxx]
    return img



#标签文件
label_file = "labels.txt"

# 读取标签文件
def readLabels():
    index = 0
    labels=[]
    with open(label_file) as file_obj:
        for line in file_obj:
            labels.append(line.strip())
            index=index+1
    return labels

labels = readLabels()

In [46]:
#读取IR模型文件
model_xml = "onnx/handwriting_from_pytorch.onnx"
net = ie.read_network(model=model_xml, weights=None)

#准备输入输出张量MYRIAD
print("Preparing input blobs")
input_blob = next(iter(net.inputs))
out_blob = next(iter(net.outputs))
net.batch_size = 1


Preparing input blobs
<ipython-input-46-9e860a6d4472>:7: DeprecationWarning: 'inputs' property of IENetwork class is deprecated. To access DataPtrs user need to use 'input_data' property of InputInfoPtr objects which can be accessed by 'input_info' property.
  input_blob = next(iter(net.inputs))


In [47]:
#载入模型到AI推断计算设备
print("Loading IR to the plugin...")
exec_net = ie.load_network(network=net, num_requests=1, device_name=DEVICE)
frame = cv.imread(image_file)
frame = cutImg(frame)
frame = cv.cvtColor(frame,cv.COLOR_BGR2RGB)
# frame = Image.fromarray(cv.cvtColor(img,cv.COLOR_BGR2RGB))
# frame = cv.resize(frame, (64,64))
# deal
n, c, h, w = net.inputs[input_blob].shape
initial_h, initial_w, channels = frame.shape
#按照AI模型要求放缩图片
image = cv.resize(frame, (w, h))  
image = preprocess(image)

print("Batch size is {}".format(n))

Loading IR to the plugin...
Batch size is 1
<ipython-input-47-bf52e68c9b26>:10: DeprecationWarning: 'inputs' property of IENetwork class is deprecated. To access DataPtrs user need to use 'input_data' property of InputInfoPtr objects which can be accessed by 'input_info' property.
  n, c, h, w = net.inputs[input_blob].shape


In [48]:

#执行推断计算
print("Starting inference in synchronous mode")
start = time.time()
res = exec_net.infer(inputs={input_blob: image})
end = time.time()
print("Infer Time:{}ms".format((end-start)*1000))
print(res)
# 处理输出
print("Processing output blob")
res = res[out_blob]
print(res)
index = np.argsort(-res[0])[0:top_k]
for c in index:
    print(labels[c])


Starting inference in synchronous mode
Infer Time:6.3915252685546875ms
{'output': array([[-88.821846, -83.00881 , -87.61913 , ..., -90.74928 , -90.11325 ,
        -87.76955 ]], dtype=float32)}
Processing output blob
[[-88.821846 -83.00881  -87.61913  ... -90.74928  -90.11325  -87.76955 ]]
余
朱
杀
朵
会
